## Q LEARNING FOR INTELLIGENT GAME PLAYING

<h3> 1. Introduction </h3>

Reinforcement learning is an area of Machine Learning Reinforcement. It is about taking suitable action to maximize reward in a situation. Reinforcement learning differs from the supervised learning in a way that in supervised learning the training data has the answer key with it so the model is trained with the correct answer itself whereas in reinforcement learning, there is no answer but the reinforcement agent decides what to do to perform the given task. In the absence of training dataset, it is bound to learn from its experience.

In [1]:
import numpy as np
import pickle

State class was defined to record the board state, available board positions, winner, rewards and game state. First, we initialized two agents, an empty board and player symbol (1 for player1 and -1 for player2). The state continuously checked if the game had ended and if it ended, checked the winner and gave reward to the agent that won.

In [6]:
class state:
    def __init__(self,a1,a2):
        self.state = '         '
        self.a1 = a1
        self.a2 = a2
        self.board = np.zeros((rows, cols)).astype(int)
        self.gameEnd = False
        self.playerSymbol = 1
        
    def getBoardState(self):
        self.BoardState = str(self.board.reshape(cols * rows))
        return self.BoardState
        
    def printBoard(self,pos):
        s = pos
        s= s.replace('0', '*')
        s= s.replace('-1', 'O')
        s= s.replace('1', 'X')
        s= s.replace('[', '')
        s= s.replace(']', '')
        s = s.replace(" ", "")
        #print(s)

        print('    -------------')
        print('    | {} | {} | {} |'.format(s[0],s[1],s[2]))
        print('    -------------')
        print('    | {} | {} | {} | '.format(s[3],s[4],s[5]))
        print('    -------------')
        print('    | {} | {} | {} | '.format(s[6],s[7],s[8]))
        print('    -------------')
        
    def availablePositions(self):
        positions = []
        for i in range(rows):
            for j in range(cols):
                if self.board[i, j] == 0:
                    positions.append((i, j))  # need to be tuple
        return positions
     
    def winner(self):
         # row
        for i in range(rows):
            if sum(self.board[i, :]) == 3:
                self.gameEnd = True
                return 1
            if sum(self.board[i, :]) == -3:
                self.gameEnd = True
                return -1
        # col
        for i in range(cols):
            if sum(self.board[:, i]) == 3:
                self.gameEnd = True
                return 1
            if sum(self.board[:, i]) == -3:
                self.gameEnd = True
                return -1
        # diagonal
        diag_sum1 = sum([self.board[i, i] for i in range(cols)])
        diag_sum2 = sum([self.board[i, cols - i - 1] for i in range(cols)])
        diag_sum = max(abs(diag_sum1), abs(diag_sum2))
        if diag_sum == 3:
            self.gameEnd = True
            if diag_sum1 == 3 or diag_sum2 == 3:
                return 1
            else:
                return -1

        # tie
        # no available positions
        if len(self.availablePositions()) == 0:
            self.gameEnd = True
            return 0
        # not end
        self.gameEnd = False
        return None

    def updateState(self, position):
        self.board[position] = self.playerSymbol
        # switch to another player
        self.playerSymbol = -1 if self.playerSymbol == 1 else 1    
    
    # only when game ends
    def Reward(self):
        result = self.winner()
        # backpropagate reward
        if result == 1:
            self.a1.giveReward(1)
            self.a2.giveReward(0)
        elif result == -1:
            self.a1.giveReward(0)
            self.a2.giveReward(1)
        else:
            self.a1.giveReward(0.1)
            self.a2.giveReward(0.5)

    # board reset
    def reset(self):
        self.board = np.zeros((rows, cols)).astype(int)
        self.BoardState = None
        self.gameEnd = False
        self.playerSymbol = 1
    
    def print_winner(self, results):
        if results == 1:
            print('Winner is Agent1 (X)' )
        elif results == -1:
            print('Winner is Agent2 (O)' )
        else:
            print('Tie')
    
    def game_state(self,result):
        alist.append(result)
        from collections import Counter 
        c= Counter(alist)
        percent= [(i, c[i] / len(alist) * 100.0) for i in c]
        #print(c)
        print("Percent of game won by each agent:",percent)
    

    def play(self, rounds=100):
        
        for i in range(rounds):
            print("Episode {}".format(i))
            if i % 1000 == 0:
                print("Rounds {}".format(i))
            while not self.gameEnd:
                # Player 1
                positions = self.availablePositions()
                a1_action = self.a1.chooseAction(positions, self.board, self.playerSymbol)
                # take action and upate board state
                self.updateState(a1_action)
                board_state = self.getBoardState()
                #self.printBoard(board_state)
                self.a1.addState(board_state)
                # check board status if it is end

                win = self.winner()
                if win is not None:
                    # self.showBoard()
                    # ended with p1 either win or draw
                    self.Reward()
                    self.a1.reset()
                    self.a2.reset()
                    self.reset()
                    break

                else:
                    # Player 2
                    positions = self.availablePositions()
                    a2_action = self.a2.chooseAction(positions, self.board, self.playerSymbol)
                    self.updateState(a2_action)
                    board_state = self.getBoardState()
                    #self.printBoard(board_state)
                    self.a2.addState(board_state)

                    win = self.winner()
                    if win is not None:
                        # self.showBoard()
                        # ended with p2 either win or draw
                        self.Reward()
                        self.a1.reset()
                        self.a2.reset()
                        self.reset()
                        break
            self.print_winner(win)
            self.game_state(win)
        
        

Class Agent is defined and basic steps in this class are described as follows:

1.	Agent starts in a state (s1) takes an action (a1) and receives a reward (r1)
2.	Agent selects action by referencing Q-table with highest value (max) OR by random (epsilon, ε)
3.	Update q-values

Q-Learning steps:

1. Create a Q- table: 
When Q-learning is performed we create what’s called a Q-table or matrix that follows the shape of [state, action] and we initialize our values to zero. We then update and store our Q-values after an episode. This q-table becomes a reference table for our agent to select the best action based on the Q-value.

2. Q-learning and making updates:
The next step is simply for the agent to interact with the environment and make updates to the state action pairs in our q-table Q[state, action], Which can be done in 2 ways. The First method is exploit, where the q-table is used as a reference to view all possible actions for a given state. The agent then selects the action based on the max value of those actions. We then use the information to make a decision.The second method is explore, which is to take action Randomly. Instead of selecting actions based on the max future reward we select an action at random. Acting randomly is important because it allows the agent to explore and discover new states that otherwise may not be selected during the exploitation process.

3. Updating the Q-Table:
The updates occur after each step or action and ends when an episode is done. Done in this case means reaching some terminal point by the agent. A terminal state for example can be anything like landing on a checkout page, reaching the end of some game, completing some desired objective, etc. The agent will not learn much after a single episode, but eventually with enough exploring (steps and episodes) it will converge and learn the optimal q-values or q-star (Q∗).

In [3]:
class Agent:
    def __init__(self, name, exp_rate=0.3):
        self.name = name
        self.states = []  # record all positions taken
        self.learn_rate = 0.5
        self.exp_rate = exp_rate
        self.gamma = 0.9
        self.states_value = {}  # state -> value
        
    def getBoardState(self, board):
        boardState = str(board.reshape(cols * rows))
        return boardState
        
    def chooseAction(self, positions, current_board, symbol):
        if np.random.uniform(0, 1) <= self.exp_rate:
            # take random action
            idx = np.random.choice(len(positions))
            action = positions[idx]
        else:
            value_max = -999
            for p in positions:
                next_board = current_board.copy()
                next_board[p] = symbol
                next_boardState = self.getBoardState(next_board)
                
                value = 0 if self.states_value.get(next_boardState) is None else self.states_value.get(next_boardState)

                # print("value", value)
                if value >= value_max:
                    value_max = value
                    action = p
        print("{} takes action {}".format(self.name, action))
        return action

    # append a hash state
    def addState(self, state):
        self.states.append(state)
        
    def Reward(self):
        result = self.winner()
        if result == 1:
            self.a1.giveReward(1)
            self.a2.giveReward(0)
        elif result == -1:
            self.a1.giveReward(0)
            self.a2.giveReward(1)
        else:
            self.a1.giveReward(-0.1)
            self.a2.giveReward(-0.1)
            

    def giveReward(self, reward):
        for st in reversed(self.states):
            if self.states_value.get(st) is None:
                self.states_value[st] = 0
            self.states_value[st] += self.learn_rate * (self.gamma * reward - self.states_value[st])
            #print(self.states_value)
            reward = self.states_value[st]

    def reset(self):
        self.states = []

    def savePolicy(self):
        fw = open('policy_' + str(self.name), 'wb')
        pickle.dump(self.states_value, fw)
        fw.close()

    def loadPolicy(self, file):
        fr = open(file,'rb')
        self.states_value = pickle.load(fr)
        fr.close()

<h3> Result and Analysis </h3>

Using the discount factor of 0.9 and Learning rate of 0.5, we obtained the draw percentage to be 95%, meaning it is almost unbeatable. It can be clearly seen from the results below that the total percentage of ‘player1’ wins is 100%, ‘player2’ is 0% and tie is 0% before learning. After 20000 learning games, the percentage win of ‘player1’ becomes 0.6%, percentage wins of ‘player2’ becomes 4% and percentage wins of ‘ties’ becomes 95%. This indicates that our agent has learnt to play completely. 

### Training with 1000 rounds

In [4]:
rows=3
cols=3
alist = []

if __name__ == "__main__":
    # training
    a1 = Agent("agent1")
    a2 = Agent("agent2")

    st = state(a1, a2)
    #print("training...")

    print(st.availablePositions())
    st.play(1000)
    a1.savePolicy()
    a2.savePolicy()

[(0, 0), (0, 1), (0, 2), (1, 0), (1, 1), (1, 2), (2, 0), (2, 1), (2, 2)]
Episode 0
Rounds 0
agent1 takes action (2, 2)
    -------------
    | * | * | * |
    -------------
    | * | * | * | 
    -------------
    | * | * | X | 
    -------------
agent2 takes action (2, 1)
    -------------
    | * | * | * |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
agent1 takes action (2, 0)
    -------------
    | * | * | * |
    -------------
    | * | * | * | 
    -------------
    | X | O | X | 
    -------------
agent2 takes action (1, 2)
    -------------
    | * | * | * |
    -------------
    | * | * | O | 
    -------------
    | X | O | X | 
    -------------
agent1 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
    | * | X | O | 
    -------------
    | X | O | X | 
    -------------
agent2 takes action (0, 0)
    -------------
    | O | * | * |
    -------------
    | * | X | O | 
    -------------
    | X | O | X

agent2 takes action (2, 2)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | * | * | O | 
    -------------
agent1 takes action (2, 1)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | * | X | O | 
    -------------
agent2 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
    | X | O | * | 
    -------------
    | * | X | O | 
    -------------
agent1 takes action (0, 0)
    -------------
    | X | * | * |
    -------------
    | X | O | * | 
    -------------
    | * | X | O | 
    -------------
agent2 takes action (2, 0)
    -------------
    | X | * | * |
    -------------
    | X | O | * | 
    -------------
    | O | X | O | 
    -------------
agent1 takes action (1, 2)
    -------------
    | X | * | * |
    -------------
    | X | O | X | 
    -------------
    | O | X | O | 
    -------------
agent2 takes action (0, 2)
    -------------
    | X | * | O |
    ---

    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | * | * | O | 
    -------------
agent1 takes action (2, 0)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | X | * | O | 
    -------------
agent2 takes action (2, 1)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | X | O | O | 
    -------------
agent1 takes action (0, 0)
    -------------
    | X | * | * |
    -------------
    | X | * | * | 
    -------------
    | X | O | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 16.43835616438356), (-1, 34.24657534246575), (1, 49.31506849315068)]
Episode 73
agent1 takes action (1, 0)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (2, 2)
    -------------
    | * | * | * |
    -------------
    | X | * | * | 
    -------

agent1 takes action (2, 1)
    -------------
    | * | * | O |
    -------------
    | X | X | * | 
    -------------
    | * | X | O | 
    -------------
agent2 takes action (2, 0)
    -------------
    | * | * | O |
    -------------
    | X | X | * | 
    -------------
    | O | X | O | 
    -------------
agent1 takes action (1, 2)
    -------------
    | * | * | O |
    -------------
    | X | X | X | 
    -------------
    | O | X | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 13.88888888888889), (-1, 31.48148148148148), (1, 54.629629629629626)]
Episode 108
agent1 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (0, 1)
    -------------
    | * | O | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent1 takes action (2, 2)
    -------------
    | * | O | * |
    -------------
 

agent1 takes action (1, 0)
    -------------
    | * | O | * |
    -------------
    | X | X | X | 
    -------------
    | O | X | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 14.788732394366196), (-1, 29.577464788732392), (1, 55.633802816901415)]
Episode 142
agent1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
agent1 takes action (2, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | X | * | 
    -------------
agent2 takes action (2, 2)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | X | O | 
    -------------
agent1 takes action (2, 0)
    -------------
    | * | O | X |
    -------------

...

agent1 takes action (2, 2)
    -------------
    | * | * | O |
    -------------
    | * | X | * | 
    -------------
    | X | O | X | 
    -------------
agent2 takes action (0, 1)
    -------------
    | * | O | O |
    -------------
    | * | X | * | 
    -------------
    | X | O | X | 
    -------------
agent1 takes action (0, 0)
    -------------
    | X | O | O |
    -------------
    | * | X | * | 
    -------------
    | X | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 15.393794749403341), (-1, 21.121718377088307), (1, 63.48448687350835)]
Episode 838
agent1 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (0, 2)
    -------------
    | * | * | O |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent1 takes action (2, 0)
    -------------
    | * | * | O |
    -------------


    | * | * | X | 
    -------------
agent2 takes action (0, 2)
    -------------
    | * | * | O |
    -------------
    | * | * | * | 
    -------------
    | * | * | X | 
    -------------
agent1 takes action (0, 0)
    -------------
    | X | * | O |
    -------------
    | * | * | * | 
    -------------
    | * | * | X | 
    -------------
agent2 takes action (2, 1)
    -------------
    | X | * | O |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
agent1 takes action (1, 1)
    -------------
    | X | * | O |
    -------------
    | * | X | * | 
    -------------
    | * | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 15.358361774744028), (-1, 20.819112627986346), (1, 63.82252559726962)]
Episode 879
agent1 takes action (2, 1)
    -------------
    | * | * | * |
    -------------
    | * | * | * | 
    -------------
    | * | X | * | 
    -------------
agent2 takes action (1, 1)
    -------------

    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 15.376226826608505), (-1, 20.93784078516903), (1, 63.68593238822247)]
Episode 917
agent1 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (0, 1)
    -------------
    | * | O | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent1 takes action (0, 0)
    -------------
    | X | O | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (2, 2)
    -------------
    | X | O | * |
    -------------
    | * | X | * | 
    -------------
    | * | * | O | 
    -------------
agent1 takes action (2, 0)
    -------------
    | X | O | * |
    -------------
    | * | X | * | 
    -------------
    | X | * | O | 
    -------------
agent2 takes action (2, 1)
    -------------
    | X | O | * |
 

agent2 takes action (2, 2)
    -------------
    | X | * | * |
    -------------
    | * | O | * | 
    -------------
    | X | * | O | 
    -------------
agent1 takes action (0, 1)
    -------------
    | X | X | * |
    -------------
    | * | O | * | 
    -------------
    | X | * | O | 
    -------------
agent2 takes action (2, 1)
    -------------
    | X | X | * |
    -------------
    | * | O | * | 
    -------------
    | X | O | O | 
    -------------
agent1 takes action (0, 2)
    -------------
    | X | X | X |
    -------------
    | * | O | * | 
    -------------
    | X | O | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 15.328467153284672), (-1, 20.5422314911366), (1, 64.12930135557873)]
Episode 959
agent1 takes action (1, 2)
    -------------
    | * | * | * |
    -------------
    | * | * | X | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (1, 1)
    -------------
    | * | * | * |
    -------------
  

    -------------
    | O | X | O | 
    -------------
Tie
Percent of game won by each agent: [(0, 15.531062124248496), (-1, 20.440881763527056), (1, 64.02805611222445)]
Episode 998
agent1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
agent2 takes action (2, 1)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | * | 
    -------------
agent1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
agent2 takes action (0, 0)
    -------------
    | O | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
agent1 takes action (1, 1)
    -------------
    | O | * | X |
    -------------
    | * | X | * | 
    -------------
    | * | O | X | 
    -------------
agent2 takes action (2, 0)
    ------------

### Testing

In [5]:
alist = []

p1 = Agent("Player1", exp_rate=0)
p1.loadPolicy("policy_agent1")

p2 = Agent("Player2", exp_rate=0)
p2.loadPolicy("policy_agent2")

st = state(p1, p2)
st.play(500)

Episode 0
Rounds 0
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (2, 1)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | * | 
    -------------
Player1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
Player1 takes action (1, 1)
    -------------
    | * | O | X |
    -------------
    | * | X | * | 
    -------------
    | * | O | X | 
    -------------
Player2 takes action (2, 0)
    -------------
    | * | O | X |
    -------------
    | * | X | * | 
    -------------
    | O | O | X | 
    -------------
Player1 takes action (1, 2)
    -------------

    | * | O | X | 
    -------------
Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
Player1 takes action (1, 1)
    -------------
    | * | O | X |
    -------------
    | * | X | * | 
    -------------
    | * | O | X | 
    -------------
Player2 takes action (2, 0)
    -------------
    | * | O | X |
    -------------
    | * | X | * | 
    -------------
    | O | O | X | 
    -------------
Player1 takes action (1, 2)
    -------------
    | * | O | X |
    -------------
    | * | X | X | 
    -------------
    | O | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 43
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
  

    -------------
    | * | X | X |
    -------------
    | * | O | X | 
    -------------
    | O | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 78
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (1, 0)
    -------------
    | * | * | X |
    -------------
    | O | * | * | 
    -------------
    | * | * | * | 
    -------------
Player1 takes action (1, 1)
    -------------
    | * | * | X |
    -------------
    | O | X | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | O | X | * | 
    -------------
    | * | * | O | 
    -------------
Player1 takes action (2, 0)
    -------------
    | * | * | X |
    -------------
    | O | X | * | 
    -------------
    | X | * | O | 
    -------------
Winner is Ag

    -------------
    | * | * | X |
    -------------
    | * | X | O | 
    -------------
    | X | * | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 114
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (2, 0)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | O | * | * | 
    -------------
Player1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | O | * | X | 
    -------------
Player2 takes action (1, 1)
    -------------
    | * | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player1 takes action (0, 0)
    -------------
    | X | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player2 tak

Player1 takes action (2, 0)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | O | 
    -------------
Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | O | 
    -------------
Player1 takes action (1, 0)
    -------------
    | * | O | X |
    -------------
    | X | * | * | 
    -------------
    | X | * | O | 
    -------------
Player2 takes action (2, 1)
    -------------
    | * | O | X |
    -------------
    | X | * | * | 
    -------------
    | X | O | O | 
    -------------
Player1 takes action (1, 1)
    -------------
    | * | O | X |
    -------------
    | X | X | * | 
    -------------
    | X | O | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 153
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
 

...

Player1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | O | * | X | 
    -------------
Player2 takes action (1, 1)
    -------------
    | * | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player1 takes action (0, 0)
    -------------
    | X | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player2 takes action (2, 1)
    -------------
    | X | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | O | X | 
    -------------
Player1 takes action (1, 2)
    -------------
    | X | * | X |
    -------------
    | * | O | X | 
    -------------
    | O | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 342
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
 

Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player1 takes action (2, 0)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | * | 
    -------------
Player2 takes action (0, 0)
    -------------
    | O | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | * | 
    -------------
Player1 takes action (2, 2)
    -------------
    | O | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | X | 
    -------------
Player2 takes action (2, 1)
    -------------
    | O | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | O | X | 
    -------------
Player1 takes action (1, 1)
    -------------
    | O | O | X |
    -------------
    | * | X | * | 
    -------------
    | X | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100

    -------------
    | * | * | * | 
    -------------
Player2 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | O | 
    -------------
Player1 takes action (2, 0)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | O | 
    -------------
Player2 takes action (0, 1)
    -------------
    | * | O | X |
    -------------
    | * | * | * | 
    -------------
    | X | * | O | 
    -------------
Player1 takes action (1, 0)
    -------------
    | * | O | X |
    -------------
    | X | * | * | 
    -------------
    | X | * | O | 
    -------------
Player2 takes action (2, 1)
    -------------
    | * | O | X |
    -------------
    | X | * | * | 
    -------------
    | X | O | O | 
    -------------
Player1 takes action (1, 1)
    -------------
    | * | O | X |
    -------------
    | X | X | * | 
    -------------
    | X | O | O | 
    -------------
Winner is

Player2 takes action (2, 0)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | O | * | * | 
    -------------
Player1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | O | * | X | 
    -------------
Player2 takes action (1, 1)
    -------------
    | * | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player1 takes action (0, 0)
    -------------
    | X | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | * | X | 
    -------------
Player2 takes action (2, 1)
    -------------
    | X | * | X |
    -------------
    | * | O | * | 
    -------------
    | O | O | X | 
    -------------
Player1 takes action (1, 2)
    -------------
    | X | * | X |
    -------------
    | * | O | X | 
    -------------
    | O | O | X | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100

Player1 takes action (1, 1)
    -------------
    | * | * | X |
    -------------
    | * | X | O | 
    -------------
    | X | * | O | 
    -------------
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 492
Player1 takes action (0, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | * | * | 
    -------------
Player2 takes action (2, 1)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | * | 
    -------------
Player1 takes action (2, 2)
    -------------
    | * | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
Player2 takes action (0, 0)
    -------------
    | O | * | X |
    -------------
    | * | * | * | 
    -------------
    | * | O | X | 
    -------------
Player1 takes action (1, 1)
    -------------
    | O | * | X |
    -------------
    | * | X | * | 
    -------------
    | * | O | X | 
 

### Training with 10000 rounds

In [7]:
rows=3
cols=3
alist = []

if __name__ == "__main__":
    # training
    a1 = Agent("agent1")
    a2 = Agent("agent2")

    st = state(a1, a2)
    #print("training...")
    st.play(10000)
    a1.savePolicy()
    a2.savePolicy()

Episode 0
Rounds 0
agent1 takes action (2, 2)
agent2 takes action (2, 1)
agent1 takes action (1, 0)
agent2 takes action (2, 0)
agent1 takes action (0, 2)
agent2 takes action (1, 2)
agent1 takes action (1, 1)
agent2 takes action (0, 1)
agent1 takes action (0, 0)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 1
agent1 takes action (2, 2)
agent2 takes action (2, 1)
agent1 takes action (1, 0)
agent2 takes action (2, 0)
agent1 takes action (1, 2)
agent2 takes action (0, 0)
agent1 takes action (1, 1)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 2
agent1 takes action (2, 2)
agent2 takes action (2, 1)
agent1 takes action (1, 0)
agent2 takes action (2, 0)
agent1 takes action (1, 2)
agent2 takes action (1, 1)
agent1 takes action (0, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 100.0)]
Episode 3
agent1 takes action (2, 0)
agent2 takes action (2, 1)
agent1 takes action (0, 1)
agent2 takes action (2, 2)
agent1 takes ac

agent1 takes action (1, 1)
agent2 takes action (1, 0)
agent1 takes action (2, 1)
agent2 takes action (1, 2)
agent1 takes action (0, 0)
agent2 takes action (0, 1)
agent1 takes action (0, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 56.17977528089888), (-1, 33.70786516853933), (0, 10.112359550561797)]
Episode 89
agent1 takes action (2, 0)
agent2 takes action (0, 2)
agent1 takes action (2, 2)
agent2 takes action (2, 1)
agent1 takes action (1, 2)
agent2 takes action (1, 1)
agent1 takes action (1, 0)
agent2 takes action (0, 0)
agent1 takes action (0, 1)
Tie
Percent of game won by each agent: [(1, 55.55555555555556), (-1, 33.33333333333333), (0, 11.11111111111111)]
Episode 90
agent1 takes action (2, 0)
agent2 takes action (0, 0)
agent1 takes action (0, 1)
agent2 takes action (2, 2)
agent1 takes action (1, 0)
agent2 takes action (2, 1)
agent1 takes action (1, 2)
agent2 takes action (1, 1)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 54.94505494505495), (-1, 

Percent of game won by each agent: [(1, 55.69620253164557), (-1, 30.37974683544304), (0, 13.924050632911392)]
Episode 158
agent1 takes action (2, 1)
agent2 takes action (1, 1)
agent1 takes action (2, 2)
agent2 takes action (2, 0)
agent1 takes action (0, 1)
agent2 takes action (1, 2)
agent1 takes action (1, 0)
agent2 takes action (0, 2)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 55.34591194968554), (-1, 30.81761006289308), (0, 13.836477987421384)]
Episode 159
agent1 takes action (1, 0)
agent2 takes action (1, 2)
agent1 takes action (2, 2)
agent2 takes action (1, 1)
agent1 takes action (2, 1)
agent2 takes action (2, 0)
agent1 takes action (0, 1)
agent2 takes action (0, 2)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 55.00000000000001), (-1, 31.25), (0, 13.750000000000002)]
Episode 160
agent1 takes action (2, 1)
agent2 takes action (0, 0)
agent1 takes action (2, 2)
agent2 takes action (1, 0)
agent1 takes action (0, 2)
agent2 takes action (0, 1)
agent1 tak

agent2 takes action (2, 0)
agent1 takes action (1, 1)
agent2 takes action (1, 2)
agent1 takes action (0, 1)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 56.84647302904564), (-1, 31.950207468879665), (0, 11.20331950207469)]
Episode 241
agent1 takes action (1, 1)
agent2 takes action (0, 2)
agent1 takes action (2, 2)
agent2 takes action (0, 0)
agent1 takes action (2, 1)
agent2 takes action (2, 0)
agent1 takes action (1, 0)
agent2 takes action (0, 1)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 56.611570247933884), (-1, 32.231404958677686), (0, 11.15702479338843)]
Episode 242
agent1 takes action (2, 1)
agent2 takes action (1, 2)
agent1 takes action (2, 2)
agent2 takes action (0, 0)
agent1 takes action (2, 0)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 56.79012345679012), (-1, 32.098765432098766), (0, 11.11111111111111)]
Episode 243
agent1 takes action (2, 1)
agent2 takes action (0, 2)
agent1 takes action (2, 2)
agent2 takes action (2, 0)
age

agent1 takes action (1, 0)
agent2 takes action (1, 2)
agent1 takes action (2, 0)
agent2 takes action (2, 1)
agent1 takes action (0, 0)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 57.3208722741433), (-1, 31.464174454828658), (0, 11.214953271028037)]
Episode 321
agent1 takes action (2, 0)
agent2 takes action (2, 1)
agent1 takes action (0, 1)
agent2 takes action (2, 2)
agent1 takes action (1, 1)
agent2 takes action (1, 2)
agent1 takes action (0, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 57.453416149068325), (-1, 31.366459627329192), (0, 11.180124223602485)]
Episode 322
agent1 takes action (0, 0)
agent2 takes action (1, 0)
agent1 takes action (0, 1)
agent2 takes action (1, 1)
agent1 takes action (2, 2)
agent2 takes action (2, 1)
agent1 takes action (0, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 57.585139318885446), (-1, 31.269349845201237), (0, 11.145510835913312)]
Episode 323
agent1 takes action (2, 2)
agent2 takes action (0, 1)


...

Percent of game won by each agent: [(1, 53.65174334639984), (-1, 27.98638332989478), (0, 18.361873323705385)]
Episode 9694
agent1 takes action (1, 1)
agent2 takes action (2, 2)
agent1 takes action (0, 0)
agent2 takes action (0, 2)
agent1 takes action (1, 2)
agent2 takes action (1, 0)
agent1 takes action (2, 1)
agent2 takes action (2, 0)
agent1 takes action (0, 1)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.65652398143372), (-1, 27.983496647756578), (0, 18.359979370809697)]
Episode 9695
agent1 takes action (2, 1)
agent2 takes action (0, 1)
agent1 takes action (2, 2)
agent2 takes action (2, 0)
agent1 takes action (0, 2)
agent2 takes action (1, 0)
agent1 takes action (0, 0)
agent2 takes action (1, 2)
agent1 takes action (1, 1)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.66130363036304), (-1, 27.980610561056107), (0, 18.358085808580856)]
Episode 9696
agent1 takes action (2, 1)
agent2 takes action (0, 2)
agent1 takes action (2, 2)
agent2 takes action 

agent1 takes action (1, 1)
agent2 takes action (2, 1)
agent1 takes action (2, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.5670356703567), (-1, 27.9930299302993), (0, 18.439934399343993)]
Episode 9756
agent1 takes action (0, 0)
agent2 takes action (2, 0)
agent1 takes action (1, 0)
agent2 takes action (0, 2)
agent1 takes action (2, 1)
agent2 takes action (2, 2)
agent1 takes action (1, 2)
agent2 takes action (1, 1)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 53.56154555703597), (-1, 28.00040996207851), (0, 18.43804448088552)]
Episode 9757
agent1 takes action (0, 0)
agent2 takes action (2, 0)
agent1 takes action (0, 1)
agent2 takes action (1, 1)
agent1 takes action (0, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.566304570608736), (-1, 27.997540479606474), (0, 18.436154949784793)]
Episode 9758
agent1 takes action (0, 0)
agent2 takes action (0, 2)
agent1 takes action (2, 0)
agent2 takes action (0, 1)
agent1 takes action (2, 2)
ag

agent2 takes action (2, 1)
agent1 takes action (0, 1)
agent2 takes action (1, 1)
agent1 takes action (1, 0)
agent2 takes action (0, 0)
agent1 takes action (0, 2)
Tie
Percent of game won by each agent: [(1, 53.56415478615071), (-1, 28.0142566191446), (0, 18.421588594704687)]
Episode 9820
agent1 takes action (2, 2)
agent2 takes action (1, 2)
agent1 takes action (2, 1)
agent2 takes action (2, 0)
agent1 takes action (1, 0)
agent2 takes action (0, 1)
agent1 takes action (1, 1)
agent2 takes action (0, 0)
agent1 takes action (0, 2)
Tie
Percent of game won by each agent: [(1, 53.55870074330517), (-1, 28.011404133998575), (0, 18.429895122696262)]
Episode 9821
agent1 takes action (2, 2)
agent2 takes action (1, 2)
agent1 takes action (0, 0)
agent2 takes action (1, 1)
agent1 takes action (0, 2)
agent2 takes action (1, 0)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 53.55324781103646), (-1, 28.018733455508045), (0, 18.42801873345551)]
Episode 9822
agent1 takes action (2, 2)
agent2 t

agent1 takes action (2, 2)
agent2 takes action (1, 2)
agent1 takes action (0, 1)
agent2 takes action (2, 1)
agent1 takes action (0, 2)
Tie
Percent of game won by each agent: [(1, 53.49919093851133), (-1, 27.993527508090615), (0, 18.50728155339806)]
Episode 9888
agent1 takes action (1, 2)
agent2 takes action (0, 2)
agent1 takes action (2, 1)
agent2 takes action (2, 2)
agent1 takes action (1, 0)
agent2 takes action (1, 1)
agent1 takes action (0, 0)
agent2 takes action (2, 0)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 53.49378096875316), (-1, 28.000808979674385), (0, 18.505410051572454)]
Episode 9889
agent1 takes action (2, 2)
agent2 takes action (2, 0)
agent1 takes action (1, 1)
agent2 takes action (2, 1)
agent1 takes action (0, 0)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.49848331648129), (-1, 27.99797775530839), (0, 18.503538928210315)]
Episode 9890
agent1 takes action (2, 2)
agent2 takes action (2, 0)
agent1 takes action (0, 2)
agent2 takes acti

agent1 takes action (0, 2)
agent2 takes action (2, 2)
agent1 takes action (0, 1)
agent2 takes action (0, 0)
agent1 takes action (1, 1)
agent2 takes action (2, 0)
Winner is Agent2 (O)
Percent of game won by each agent: [(1, 53.46663987138264), (-1, 28.044614147909968), (0, 18.488745980707396)]
Episode 9952
agent1 takes action (2, 1)
agent2 takes action (0, 0)
agent1 takes action (2, 0)
agent2 takes action (2, 2)
agent1 takes action (1, 1)
agent2 takes action (0, 2)
agent1 takes action (0, 1)
Winner is Agent1 (X)
Percent of game won by each agent: [(1, 53.47131518135235), (-1, 28.041796443283435), (0, 18.48688837536421)]
Episode 9953
agent1 takes action (2, 1)
agent2 takes action (1, 1)
agent1 takes action (1, 2)
agent2 takes action (2, 2)
agent1 takes action (0, 0)
agent2 takes action (2, 0)
agent1 takes action (0, 2)
agent2 takes action (0, 1)
agent1 takes action (1, 0)
Tie
Percent of game won by each agent: [(1, 53.46594333936107), (-1, 28.03897930480209), (0, 18.49507735583685)]
Epis

### Testing

In [8]:
alist = []

p1 = Agent("Player1", exp_rate=0)
p1.loadPolicy("policy_agent1")

p2 = Agent("Player2", exp_rate=0)
p2.loadPolicy("policy_agent2")

st = state(p1, p2)
st.play(500)

Episode 0
Rounds 0
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 100.0)]
Episode 1
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 100.0)]
Episode 2
Player1 takes action (2, 2)
Player2 takes action (1, 1)
Player1 takes action (2, 1)
Player2 takes action (2, 0)
Player1 takes action (0, 2)
Player2 takes action (1, 0)
Player1 takes action (1, 2)
Winner is Agent1 (X)
Percent of game won by each agent: [(0, 66.66666666666666), (1, 33.33333333333333)]
Episode 3
Player1 takes action (2, 2)
Player2 takes 

Player2 takes action (1, 1)
Player1 takes action (1, 0)
Player2 takes action (0, 0)
Player1 takes action (2, 2)
Player2 takes action (2, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 2)
Winner is Agent2 (O)
Percent of game won by each agent: [(0, 79.36507936507937), (1, 1.5873015873015872), (-1, 19.047619047619047)]
Episode 63
Player1 takes action (2, 0)
Player2 takes action (1, 1)
Player1 takes action (1, 0)
Player2 takes action (0, 0)
Player1 takes action (2, 2)
Player2 takes action (2, 1)
Player1 takes action (0, 1)
Player2 takes action (1, 2)
Player1 takes action (0, 2)
Tie
Percent of game won by each agent: [(0, 79.6875), (1, 1.5625), (-1, 18.75)]
Episode 64
Player1 takes action (1, 0)
Player2 takes action (1, 1)
Player1 takes action (2, 2)
Player2 takes action (2, 1)
Player1 takes action (0, 0)
Player2 takes action (2, 0)
Player1 takes action (0, 1)
Player2 takes action (0, 2)
Winner is Agent2 (O)
Percent of game won by each agent: [(0, 78.46153846153847), (1, 1.5384615

Player2 takes action (2, 0)
Player1 takes action (0, 2)
Player2 takes action (1, 2)
Player1 takes action (1, 0)
Player2 takes action (0, 1)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 84.29752066115702), (1, 2.479338842975207), (-1, 13.223140495867769)]
Episode 121
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 84.42622950819673), (1, 2.459016393442623), (-1, 13.114754098360656)]
Episode 122
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 84.5528455284553), (1, 2.4390243

Player1 takes action (0, 0)
Player2 takes action (0, 2)
Player1 takes action (2, 0)
Player2 takes action (1, 0)
Player1 takes action (1, 2)
Tie
Percent of game won by each agent: [(0, 87.35632183908046), (1, 1.7241379310344827), (-1, 10.919540229885058)]
Episode 174
Player1 takes action (2, 2)
Player2 takes action (1, 1)
Player1 takes action (1, 2)
Player2 takes action (0, 2)
Player1 takes action (2, 0)
Player2 takes action (2, 1)
Player1 takes action (0, 1)
Player2 takes action (0, 0)
Player1 takes action (1, 0)
Tie
Percent of game won by each agent: [(0, 87.42857142857143), (1, 1.7142857142857144), (-1, 10.857142857142858)]
Episode 175
Player1 takes action (2, 0)
Player2 takes action (1, 1)
Player1 takes action (1, 2)
Player2 takes action (0, 2)
Player1 takes action (0, 1)
Player2 takes action (2, 1)
Player1 takes action (0, 0)
Player2 takes action (1, 0)
Player1 takes action (2, 2)
Tie
Percent of game won by each agent: [(0, 87.5), (1, 1.7045454545454544), (-1, 10.795454545454545)]


Player1 takes action (0, 1)
Player2 takes action (2, 1)
Player1 takes action (2, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 90.67796610169492), (1, 1.2711864406779663), (-1, 8.050847457627118)]
Episode 236
Player1 takes action (1, 2)
Player2 takes action (1, 1)
Player1 takes action (2, 1)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Player2 takes action (2, 2)
Player1 takes action (0, 2)
Player2 takes action (0, 1)
Player1 takes action (1, 0)
Tie
Percent of game won by each agent: [(0, 90.71729957805907), (1, 1.2658227848101267), (-1, 8.016877637130802)]
Episode 237
Player1 takes action (1, 2)
Player2 takes action (1, 1)
Player1 takes action (2, 1)
Player2 takes action (2, 2)
Player1 takes action (0, 0)
Player2 takes action (2, 0)
Player1 takes action (0, 2)
Player2 takes action (0, 1)
Player1 takes action (1, 0)
Tie
Percent of game won by each agent: [(0, 90.7

Player1 takes action (0, 0)
Player2 takes action (2, 2)
Player1 takes action (0, 2)
Player2 takes action (0, 1)
Player1 takes action (1, 0)
Tie
Percent of game won by each agent: [(0, 92.46575342465754), (1, 1.0273972602739725), (-1, 6.506849315068493)]
Episode 292
Player1 takes action (1, 2)
Player2 takes action (1, 1)
Player1 takes action (2, 1)
Player2 takes action (2, 2)
Player1 takes action (0, 0)
Player2 takes action (2, 0)
Player1 takes action (0, 2)
Player2 takes action (0, 1)
Player1 takes action (1, 0)
Tie
Percent of game won by each agent: [(0, 92.4914675767918), (1, 1.023890784982935), (-1, 6.484641638225256)]
Episode 293
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 92.51700680272108), (1, 1.0204081632653061), (-1, 6.4625850340

Player2 takes action (0, 2)
Player1 takes action (2, 0)
Player2 takes action (1, 0)
Player1 takes action (1, 2)
Tie
Percent of game won by each agent: [(0, 93.73219373219374), (1, 0.8547008547008548), (-1, 5.413105413105413)]
Episode 351
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 93.75), (1, 0.8522727272727272), (-1, 5.3977272727272725)]
Episode 352
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 93.76770538243626), (1, 0.84985835694051), (-1, 5.382436260623229)]
Episode 353
Player1 takes actio

Player2 takes action (0, 0)
Player1 takes action (2, 2)
Player2 takes action (1, 2)
Player1 takes action (0, 1)
Tie
Percent of game won by each agent: [(0, 94.58128078817734), (1, 0.7389162561576355), (-1, 4.679802955665025)]
Episode 406
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 94.5945945945946), (1, 0.7371007371007371), (-1, 4.668304668304668)]
Episode 407
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (1, 0)
Player2 takes action (1, 2)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 94.6078431372549), (1, 0.7352941176470588), (-1, 4.6568627450980395)]
Episode 408
Player1

Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 95.26881720430107), (1, 0.6451612903225806), (-1, 4.086021505376344)]
Episode 465
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (0, 2)
Player2 takes action (2, 0)
Player1 takes action (0, 0)
Tie
Percent of game won by each agent: [(0, 95.27896995708154), (1, 0.6437768240343348), (-1, 4.07725321888412)]
Episode 466
Player1 takes action (1, 1)
Player2 takes action (2, 2)
Player1 takes action (0, 0)
Player2 takes action (0, 2)
Player1 takes action (1, 2)
Player2 takes action (1, 0)
Player1 takes action (2, 1)
Player2 takes action (0, 1)
Player1 takes action (2, 0)
Tie
Percent of game won by each agent: [(0, 95.28907922912205), (1, 0.6423982869379015), (-1, 4.068522483940043)]
Episode 467
Player1 takes action (0, 1)
Player2 takes action (1, 1)
Player1 takes action (2, 2)
Player2

<h3> Conclusion </h3>

After 10,000 training games against itself, the Q Learned Player learns to play optimally resulting in draws in all self-play games. It would be instructive, however, to check this by pitting it against a player following the minimax algorithm for many games. As mentioned above, the agent was trained using Q learning and made it play with itself until they tie. As it played again and again, it imitates and learns the moves and thus learns to play well.  

<h3> References </h3>

1. https://github.com/MJeremy2017/Reinforcement-Learning-Implementation/blob/master/TicTacToe/ticTacToe.py
2. https://deeplizard.com/learn/video/qhRNvCVVJaA